### Imports

In [2]:
import pandas as pd
import numpy as np
from math import sqrt
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LinearRegression, SGDRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.neighbors import KNeighborsRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.svm import SVR

### Load Data

In [4]:
df = pd.read_csv('data/laptop_price_wf.csv', encoding = 'latin-1', index_col = [0])
df.head()

laptop_ID Company      Product   TypeName  Inches  \
0          1   Apple  MacBook Pro  Ultrabook    13.3   
1          2   Apple  Macbook Air  Ultrabook    13.3   
2          3      HP       250 G6   Notebook    15.6   
3          4   Apple  MacBook Pro  Ultrabook    15.4   
4          5   Apple  MacBook Pro  Ultrabook    13.3   

                     ScreenResolution                         Cpu   Ram  \
0  IPS Panel Retina Display 2560x1600        Intel Core i5 2.3GHz   8GB   
1                            1440x900        Intel Core i5 1.8GHz   8GB   
2                   Full HD 1920x1080  Intel Core i5 7200U 2.5GHz   8GB   
3  IPS Panel Retina Display 2880x1800        Intel Core i7 2.7GHz  16GB   
4  IPS Panel Retina Display 2560x1600        Intel Core i5 3.1GHz   8GB   

                Memory                           Gpu  OpSys  Price_euros  \
0            128GB SSD  Intel Iris Plus Graphics 640  macOS      1339.69   
1  128GB Flash Storage        Intel HD Graphics 6000  macOS       898.94   
2            256GB SSD         Intel HD Graphics 620  No OS       575.00   
3            512GB SSD            AMD Radeon Pro 455  macOS      2537.45   
4            256GB SSD  Intel Iris Plus Graphics 650  macOS      1803.60   

   Weight_fl  
0       1.37  
1       1.34  
2       1.86  
3       1.83  
4       1.37

### Function for Preprocessing

In [9]:
# function that preprocesses dataframe
def process_dataframe(input_df):
    # screen resolution
    input_df['Touchscreen'] = np.where(input_df['ScreenResolution'].str.contains('Touchscreen', case = False, na = False), 1, 0)
    input_df['ScreenResolution'] = input_df.apply(lambda x: x['ScreenResolution'][-8:], axis = 1)
    input_df['ScreenResolution'] = input_df['ScreenResolution'].str.replace(' ', '')
    # cpu
    input_df['Cpu'] = input_df['Cpu'].str.replace('Core', '')
    input_df['Cpu'] = input_df['Cpu'].str.split().str[:2].str.join(sep = ' ')
    input_df['Cpu'] = input_df['Cpu'].str.split().str[1:].str.join(sep = ' ')
    # memory
    input_df['ssd'] = np.where(input_df['Memory'].str.contains('ssd|hybrid', case = False, na = False), 1, 0)
    input_df['Memory'] = input_df['Memory'].str.replace('1.0', '1', regex = False)
    input_df['Memory'] = input_df['Memory'].str.replace('1TB', '1024')
    input_df['Memory'] = input_df['Memory'].str.replace('2TB', '2048')
    input_df['Memory'] = input_df['Memory'].str.replace('GB', '')
    input_df['Memory'] = input_df['Memory'].str.split().apply(lambda x: [a for a in x if a.isdigit()])
    input_df['Memory'] = input_df['Memory'].apply(lambda x: [int(a) for a in x])
    input_df['Memory'] = input_df['Memory'].apply(lambda x: sum(x))
    # gpu
    input_df['Gpu'] = input_df['Gpu'].str.split().str[:2].str.join(sep = ' ')
    input_df['Gpu'] = input_df['Gpu'].str.split().str[1:].str.join(sep = ' ')
    # drop columns
    input_df = input_df.drop(['Product', 'laptop_ID'], axis = 1)
    # drop rows
    counts_col2 = input_df.groupby('Cpu')['Cpu'].transform(len)
    counts_col3 = input_df.groupby('Gpu')['Gpu'].transform(len)
    mask = (counts_col2 > 3) & (counts_col3 > 3)
    return input_df[mask]

### Function for Pipeline

In [6]:
# Data Preprocessing
categorical_preprocessing = Pipeline([('ohe', OneHotEncoder())])
numerical_preprocessing = Pipeline([('stdscaler', StandardScaler())])

# Applying Transformer 
preprocess = ColumnTransformer([
    ('categorical_preprocessing', categorical_preprocessing, ['Company', 'TypeName', 'ScreenResolution', 'Cpu', 'Ram', 'Gpu', 'OpSys', 'Cpu_brand', 'Gpu_brand']),
    ('numerical_preprocessing', numerical_preprocessing, ['Inches', 'Memory', 'Weight_fl'])
])

# function that produces performance of pipeline with indicated model
def main(input_df, input_model):
    pipeline = Pipeline([
        ('preprocess', preprocess),
        ('model', input_model)
    ])

    X = df.drop('Price_euros', axis = 1)
    y = df['Price_euros']
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.25, random_state = 23)

    pipeline.fit(X_train, y_train)

    y_pred = pipeline.predict(X_test)

    print('MSE is: ' + str(mean_squared_error(y_test, y_pred)))
    print('RMSE is: ' + str(sqrt(mean_squared_error(y_test, y_pred))))
    print('MAE is: ' + str(mean_absolute_error(y_test, y_pred)))

In [7]:
df = process_dataframe(df)

In [18]:
# linear regression
model = LinearRegression()
main(df, model)

MSE is: 106138.2510155169
RMSE is: 325.78866004745606
MAE is: 233.05009895723583


Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('categorical_preprocessing',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder())]),
                                                  ['Company', 'TypeName',
                                                   'ScreenResolution', 'Cpu',
                                                   'Ram', 'Gpu', 'OpSys',
                                                   'Cpu_brand', 'Gpu_brand']),
                                                 ('numerical_preprocessing',
                                                  Pipeline(steps=[('stdscaler',
                                                                   StandardScaler())]),
                                                  ['Inches', 'Memory',
                                                   'Weight_fl'])])),
                ('model', LinearRegress

In [19]:
# stochastic gradient descent regression
model = SGDRegressor()
main(df, model)

MSE is: 109243.17172961908
RMSE is: 330.5195481807681
MAE is: 234.4691534962792


Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('categorical_preprocessing',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder())]),
                                                  ['Company', 'TypeName',
                                                   'ScreenResolution', 'Cpu',
                                                   'Ram', 'Gpu', 'OpSys',
                                                   'Cpu_brand', 'Gpu_brand']),
                                                 ('numerical_preprocessing',
                                                  Pipeline(steps=[('stdscaler',
                                                                   StandardScaler())]),
                                                  ['Inches', 'Memory',
                                                   'Weight_fl'])])),
                ('model', SGDRegressor(

In [20]:
# K-nearest neighbors regression
model = KNeighborsRegressor()
main(df, model)

MSE is: 103449.16395211112
RMSE is: 321.6351410404515
MAE is: 212.02324074074073


Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('categorical_preprocessing',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder())]),
                                                  ['Company', 'TypeName',
                                                   'ScreenResolution', 'Cpu',
                                                   'Ram', 'Gpu', 'OpSys',
                                                   'Cpu_brand', 'Gpu_brand']),
                                                 ('numerical_preprocessing',
                                                  Pipeline(steps=[('stdscaler',
                                                                   StandardScaler())]),
                                                  ['Inches', 'Memory',
                                                   'Weight_fl'])])),
                ('model', KNeighborsReg

In [21]:
# random forest regression
model = RandomForestRegressor()
main(df, model)

MSE is: 92954.52074482443
RMSE is: 304.88443834480046
MAE is: 205.14563716943465


Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('categorical_preprocessing',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder())]),
                                                  ['Company', 'TypeName',
                                                   'ScreenResolution', 'Cpu',
                                                   'Ram', 'Gpu', 'OpSys',
                                                   'Cpu_brand', 'Gpu_brand']),
                                                 ('numerical_preprocessing',
                                                  Pipeline(steps=[('stdscaler',
                                                                   StandardScaler())]),
                                                  ['Inches', 'Memory',
                                                   'Weight_fl'])])),
                ('model', RandomForestR

In [22]:
# xgboost regression
model = GradientBoostingRegressor()
main(df, model)

MSE is: 99955.00771942486
RMSE is: 316.1566189713966
MAE is: 218.65279181515956


Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('categorical_preprocessing',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder())]),
                                                  ['Company', 'TypeName',
                                                   'ScreenResolution', 'Cpu',
                                                   'Ram', 'Gpu', 'OpSys',
                                                   'Cpu_brand', 'Gpu_brand']),
                                                 ('numerical_preprocessing',
                                                  Pipeline(steps=[('stdscaler',
                                                                   StandardScaler())]),
                                                  ['Inches', 'Memory',
                                                   'Weight_fl'])])),
                ('model', GradientBoost

In [23]:
# support vector machine regression
model = SVR()
main(df, model)

MSE is: 507171.6591860877
RMSE is: 712.1598550789616
MAE is: 510.0649214806689


Pipeline(steps=[('preprocess',
                 ColumnTransformer(transformers=[('categorical_preprocessing',
                                                  Pipeline(steps=[('ohe',
                                                                   OneHotEncoder())]),
                                                  ['Company', 'TypeName',
                                                   'ScreenResolution', 'Cpu',
                                                   'Ram', 'Gpu', 'OpSys',
                                                   'Cpu_brand', 'Gpu_brand']),
                                                 ('numerical_preprocessing',
                                                  Pipeline(steps=[('stdscaler',
                                                                   StandardScaler())]),
                                                  ['Inches', 'Memory',
                                                   'Weight_fl'])])),
                ('model', SVR())])

### Grid Search

In [27]:
# setting up parameters grid
param_grid = {'model__n_estimators': [100, 500, 1000],
              'model__max_depth': [None, 10, 20],
              'model__min_samples_split': [2, 5, 10],
              'model__min_samples_leaf': [1, 2, 4],
              'model__max_features': ['sqrt', None, 1],
              'model__bootstrap': [True, False]}

# best performing model
pipeline = Pipeline([
    ('preprocess', preprocess),
    ('model', RandomForestRegressor())
])
X = df.drop('Price_euros', axis = 1)
y = df['Price_euros']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.25, random_state = 23)
pipeline.fit(X_train, y_train)
y_pred = pipeline.predict(X_test)

# Creating gridsearch object
grid_search = GridSearchCV(pipeline, param_grid, verbose = 10, refit = True)

In [28]:
grid_search.fit(X_train, y_train)

Fitting 5 folds for each of 486 candidates, totalling 2430 fits
[CV 1/5; 1/486] START model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100
[CV 1/5; 1/486] END model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100;, score=0.787 total time=   0.2s
[CV 2/5; 1/486] START model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100


c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 418, in _passthrough_scorer
    return estimator.score(*args, **kwargs)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\utils\metaestimators.py", line 113, in <lambda>
    out = lambda *args, **kwargs: self.fn(obj, *args, **kwargs)  # noqa
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\pipeline.py", line 707, in score
    Xt = transform.transform(Xt)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\compose\_column_transformer.py", line 748, in transform
    Xs = self._fit_trans

[CV 2/5; 1/486] END model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100;, score=nan total time=   0.2s
[CV 3/5; 1/486] START model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100


c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 418, in _passthrough_scorer
    return estimator.score(*args, **kwargs)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\utils\metaestimators.py", line 113, in <lambda>
    out = lambda *args, **kwargs: self.fn(obj, *args, **kwargs)  # noqa
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\pipeline.py", line 707, in score
    Xt = transform.transform(Xt)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\compose\_column_transformer.py", line 748, in transform
    Xs = self._fit_trans

[CV 3/5; 1/486] END model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100;, score=nan total time=   0.2s
[CV 4/5; 1/486] START model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100
[CV 4/5; 1/486] END model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100;, score=0.847 total time=   0.2s
[CV 5/5; 1/486] START model__bootstrap=True, model__max_depth=None, model__max_features=sqrt, model__min_samples_leaf=1, model__min_samples_split=2, model__n_estimators=100


...

c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 418, in _passthrough_scorer
    return estimator.score(*args, **kwargs)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\utils\metaestimators.py", line 113, in <lambda>
    out = lambda *args, **kwargs: self.fn(obj, *args, **kwargs)  # noqa
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\pipeline.py", line 707, in score
    Xt = transform.transform(Xt)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\compose\_column_transformer.py", line 748, in transform
    Xs = self._fit_trans

[CV 3/5; 486/486] END model__bootstrap=False, model__max_depth=20, model__max_features=1, model__min_samples_leaf=4, model__min_samples_split=10, model__n_estimators=1000;, score=nan total time=   0.4s
[CV 4/5; 486/486] START model__bootstrap=False, model__max_depth=20, model__max_features=1, model__min_samples_leaf=4, model__min_samples_split=10, model__n_estimators=1000
[CV 4/5; 486/486] END model__bootstrap=False, model__max_depth=20, model__max_features=1, model__min_samples_leaf=4, model__min_samples_split=10, model__n_estimators=1000;, score=0.268 total time=   0.5s
[CV 5/5; 486/486] START model__bootstrap=False, model__max_depth=20, model__max_features=1, model__min_samples_leaf=4, model__min_samples_split=10, model__n_estimators=1000


c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:770: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 761, in _score
    scores = scorer(estimator, X_test, y_test)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\metrics\_scorer.py", line 418, in _passthrough_scorer
    return estimator.score(*args, **kwargs)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\utils\metaestimators.py", line 113, in <lambda>
    out = lambda *args, **kwargs: self.fn(obj, *args, **kwargs)  # noqa
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\pipeline.py", line 707, in score
    Xt = transform.transform(Xt)
  File "c:\Users\james\anaconda3\lib\site-packages\sklearn\compose\_column_transformer.py", line 748, in transform
    Xs = self._fit_trans

[CV 5/5; 486/486] END model__bootstrap=False, model__max_depth=20, model__max_features=1, model__min_samples_leaf=4, model__min_samples_split=10, model__n_estimators=1000;, score=nan total time=   0.4s


GridSearchCV(estimator=Pipeline(steps=[('preprocess',
                                        ColumnTransformer(transformers=[('categorical_preprocessing',
                                                                         Pipeline(steps=[('ohe',
                                                                                          OneHotEncoder())]),
                                                                         ['Company',
                                                                          'TypeName',
                                                                          'ScreenResolution',
                                                                          'Cpu',
                                                                          'Ram',
                                                                          'Gpu',
                                                                          'OpSys',
                                              

In [29]:
# Print best parameters
print(grid_search.best_params_)

{'model__bootstrap': True, 'model__max_depth': None, 'model__max_features': 'sqrt', 'model__min_samples_leaf': 1, 'model__min_samples_split': 2, 'model__n_estimators': 100}


In [10]:
# tuned hyperparameters
pipeline = Pipeline([
    ('preprocess', preprocess),
    ('model', RandomForestRegressor(n_estimators = 100, 
                                    max_depth = None, 
                                    min_samples_split = 2, 
                                    min_samples_leaf = 1,
                                    max_features = 'sqrt',
                                    bootstrap = True))])
X = df.drop('Price_euros', axis = 1)
y = df['Price_euros']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.25, random_state = 23)
pipeline.fit(X_train, y_train)
y_pred = pipeline.predict(X_test)

print('MSE is: ' + str(mean_squared_error(y_test, y_pred)))
print('RMSE is: ' + str(sqrt(mean_squared_error(y_test, y_pred))))
print('MAE is: ' + str(mean_absolute_error(y_test, y_pred)))

MSE is: 83780.74402879924
RMSE is: 289.4490352873874
MAE is: 196.03426352238213
